# DEDS Werkcollege 2.2

## Imports

In [2]:
import pyodbc
import sqlite3 as sql
import pandas as pd

## Connectie SSMS

In [3]:
DB = {
    "servername" : r"VISSIE\SQLEXPRESS",
    "database" : "SDM"}

export_conn = pyodbc.connect(f"""DRIVER={'SQL SERVER'};
                             SERVER={DB['servername']};
                             DATABASE={DB['database']};
                             Trusted_Connection=yes
                             """)
export_cursor = export_conn.cursor()

## Connecties SQL Databases (raw)

In [4]:
connection_crm = sql.connect(r"..\..\..\data\raw\go_crm_train.sqlite")
connection_sales = sql.connect(r"..\..\..\data\raw\go_sales_train.sqlite")
connection_staff = sql.connect(r"..\..\..\data\raw\go_staff_train.sqlite")

## Dataframes
alle tabelnamen worden opgehaald door de create_dataframes_sql functie. Alle gelezen dataframes worden in een dictionary gestopt, met als key de tabel naam.

In [5]:
def create_dataframes_sql(connection, db_type : str):
    dictionary : dict = {}
    query : str = ""
    key : str = ""
    
    if (db_type == "sqlite"):
        query = "SELECT name FROM sqlite_master WHERE type='table';"
        key = "name"
    elif (db_type == "ssms"):
        query = "SELECT TABLE_NAME FROM INFORMATION_SCHEMA.TABLES WHERE TABLE_TYPE = 'BASE TABLE';"
        key = "TABLE_NAME"
    
    table_names = pd.read_sql(query, connection)
    
    for table in table_names[key].tolist():
        dictionary[table] = pd.read_sql(f"SELECT * FROM {table}", connection)
    
    return dictionary

crm = create_dataframes_sql(connection_crm, "sqlite")
sales = create_dataframes_sql(connection_sales, "sqlite")
staff = create_dataframes_sql(connection_staff, "sqlite")
sdm = create_dataframes_sql(export_conn, "ssms")

C:\Users\jdvis_x5odeao\AppData\Local\Temp\ipykernel_11764\1524804024.py:13: UserWarning: pandas only supports SQLAlchemy connectable (engine/connection) or database string URI or sqlite3 DBAPI2 connection. Other DBAPI2 objects are not tested. Please consider using SQLAlchemy.
  table_names = pd.read_sql(query, connection)
C:\Users\jdvis_x5odeao\AppData\Local\Temp\ipykernel_11764\1524804024.py:16: UserWarning: pandas only supports SQLAlchemy connectable (engine/connection) or database string URI or sqlite3 DBAPI2 connection. Other DBAPI2 objects are not tested. Please consider using SQLAlchemy.
  dictionary[table] = pd.read_sql(f"SELECT * FROM {table}", connection)
C:\Users\jdvis_x5odeao\AppData\Local\Temp\ipykernel_11764\1524804024.py:16: UserWarning: pandas only supports SQLAlchemy connectable (engine/connection) or database string URI or sqlite3 DBAPI2 connection. Other DBAPI2 objects are not tested. Please consider using SQLAlchemy.
  dictionary[table] = pd.read_sql(f"SELECT * FROM 

## Query runners

In [48]:
from typing import Iterable


def query_remove(table_name : str):
    try:
        query = f"TRUNCATE {table_name}"
    except pyodbc.Error:
        print(query)
        return table_name
    
    return None

def create_add_query(row):
    query = ""
    columns = list(row.keys())
    
    for pos in range(len(columns)):
        if (pos == len(columns) - 1):
            query += f"{columns[pos]}) VALUES ("
        else:
            query += f"{columns[pos]}, "
    
    data = list(row)
    
    for pos in range(len(data)):
        if (pos == len(data) - 1):
            query += f"{data[pos]})"
        else:
            query += f"{data[pos]}, "
    
    return query

def query_add(table_name : str, table_data : pd.DataFrame):
    for index, row in table_data.iterrows():
        query : str = f"INSERT INTO {table_name} ("
        query += create_add_query(row)
        print(query)
        

## Leegmaken SDM Database

In [7]:
tables_sdm = list(sdm.keys())

while len(tables_sdm) > 0:
    for table in tables_sdm:
        temp = query_remove(table)
        
        tables_sdm.remove(table)
        
        if (temp != None):
            tables_sdm.add(temp)

print("All items are removed")

All items are removed


## Toevoegen data SDM Database

In [49]:
def primary_key_detection(dataframe : pd.DataFrame):
    unique = dataframe.nunique() == len(dataframe)
    non_null = dataframe.isnull().sum() == 0
    
    return dataframe.columns[unique & non_null].tolist()

def check_primary_key(possible_key, dataframe : pd.DataFrame):
    values : list = []
    for index, row in dataframe.iterrows():
        if row[possible_key] not in values:
            values.append(row[possible_key])
        else:
            return False
    
    return True

def combine_frames(dataframe1 : pd.DataFrame, dataframe2 : pd.DataFrame):
    columns_df1 = dataframe1.columns
    columns_df2 = dataframe2.columns
 
    for column in columns_df2:
        if column not in columns_df1:
            dataframe1[column] = dataframe2[column]
    
    return dataframe1

def merge_double_tables(keys1 : list, keys2 : list, dict1 : dict, dict2 : dict):
    primary_key = ""
    
    for key in keys1:
        if key in keys2:
            possible_keys_1 = primary_key_detection(dict1[key])
            possible_keys_2 = primary_key_detection(dict2[key])
            
            for possible_primary_key in possible_keys_1:
                if possible_primary_key in possible_keys_2:
                    if (check_primary_key(possible_primary_key, dict2[key])):
                        primary_key = possible_primary_key
                        break
            
            combine_frames(dict1[key], dict2[key])
            
            dict2.pop(key)
    
    return dict1, dict2

def merge_all_in_one(dict1 : dict, dict2: dict):
    keys = list(dict2.keys())
    
    for key in keys:
        dict1[key] = dict2[key]
    
    return dict1
        
    
crm_keys = list(crm.keys())
sales_keys = list(sales.keys())
staff_keys = list(staff.keys())
all_keys = []
bundle = {}

primary_key = False
sdm = {}

crm, sales = merge_double_tables(crm_keys, sales_keys, crm, sales)
crm, staff = merge_double_tables(crm_keys, staff_keys, crm, staff)
sdm = merge_all_in_one(sdm, crm)
sdm = merge_all_in_one(sdm, sales)
sdm = merge_all_in_one(sdm, staff)

sdm_keys = list(sdm.keys())
#for key in crm_keys:
#    if key in sales_keys:
#        possible_keys_crm = primary_key_detection(crm[key])
#        possible_keys_sales = primary_key_detection(sales[key])
        
#        for possible_primary_key in possible_keys_crm:
#            if possible_primary_key in possible_keys_sales:
#                if (check_primary_key(possible_primary_key, sales[key])):
#                    primary_key = possible_primary_key
#                    break
        
#        combine_frames(crm[key], sales[key])
#        sales.pop(key)
    
for key in sdm_keys:
    query_add(key, sdm[key])

INSERT INTO age_group (AGE_GROUP_CODE, UPPER_AGE, LOWER_AGE) VALUES (1, 20, 0)
INSERT INTO age_group (AGE_GROUP_CODE, UPPER_AGE, LOWER_AGE) VALUES (2, 30, 21)
INSERT INTO age_group (AGE_GROUP_CODE, UPPER_AGE, LOWER_AGE) VALUES (3, 40, 31)
INSERT INTO age_group (AGE_GROUP_CODE, UPPER_AGE, LOWER_AGE) VALUES (4, 50, 41)
INSERT INTO age_group (AGE_GROUP_CODE, UPPER_AGE, LOWER_AGE) VALUES (5, 60, 51)
INSERT INTO age_group (AGE_GROUP_CODE, UPPER_AGE, LOWER_AGE) VALUES (6, 70, 61)
INSERT INTO country (COUNTRY_CODE, COUNTRY_EN, FLAG_IMAGE, SALES_TERRITORY_CODE, COUNTRY, LANGUAGE, CURRENCY_NAME) VALUES (1, France, F01, 6, France, EN, francs)
INSERT INTO country (COUNTRY_CODE, COUNTRY_EN, FLAG_IMAGE, SALES_TERRITORY_CODE, COUNTRY, LANGUAGE, CURRENCY_NAME) VALUES (2, Germany, F02, 6, Germany, EN, marks)
INSERT INTO country (COUNTRY_CODE, COUNTRY_EN, FLAG_IMAGE, SALES_TERRITORY_CODE, COUNTRY, LANGUAGE, CURRENCY_NAME) VALUES (3, United States, F03, 1, United States, EN, dollars)
INSERT INTO country